In [1]:
import nltk
from nltk import word_tokenize
from nltk import FreqDist
from nltk.stem import PorterStemmer
import pandas as pd
porter = PorterStemmer()
from sklearn.feature_extraction.text import TfidfVectorizer
import altair as alt
alt.renderers.enable('default')
alt.data_transformers.enable('default', max_rows=None)

DataTransformerRegistry.enable('default')

In [2]:
from nltk.corpus import stopwords
stop_words = set(stopwords.words('english'))

In [3]:
filmscript=pd.read_csv('cleaned_pudding_public_scripts.csv')

In [4]:
filmscript_10=filmscript.sample(n=10)
# films_year=filmscript.groupby('year')

In [5]:
# all script unique words
documents = filmscript.script.tolist() #to list is a built in method--turns a column to a list
vectorizer = TfidfVectorizer(max_df=.7, min_df=1, stop_words=stop_words)  #way of transforming data--representing text through their frequencies
transformed_documents = vectorizer.fit_transform(documents)
transformed_documents_as_array = transformed_documents.toarray()
link = filmscript.link.tolist()
tfidf_results = []
for counter, doc in enumerate(transformed_documents_as_array):
    # construct a dataframe
    tf_idf_tuples = list(zip(vectorizer.get_feature_names_out(), doc))
    one_doc_as_df = pd.DataFrame.from_records(tf_idf_tuples, columns=['term', 'score']).sort_values(by='score', ascending=False).reset_index(drop=True)
    one_doc_as_df['link'] = link[counter]
    tfidf_results.append(one_doc_as_df)
tfidf_df = pd.concat(tfidf_results)
tfidf_df = tfidf_df.sort_values(by=['score'], ascending=False)
# tfidf_df.head(10)
# tfidf_df[0:10]

In [6]:
# tfidf_df[:10]

In [7]:
merged=pd.merge(tfidf_df, filmscript)
merged_clean=merged.drop(columns=['imdb_id', 'script_id', 'gross_ia', 'status_code', 'script_length'])
merged_clean=merged_clean.sort_values(by=['score'], ascending=False)

In [8]:
merged2=merged_clean[:10]
# merged2

In [9]:
#step 1
alt.Chart(merged2).mark_point().encode(
    alt.X('term'),
    alt.Y('score'),
    alt.Color('title')
)

alt.Chart(...)

In [10]:
#step 2

listscript=list(filmscript.link.unique())
listscript1=listscript[:5]
def looping(ruh):
    rows=[]
    for links in ruh:
        temprow=tfidf_df[tfidf_df.link==links].sort_values(by=['score'], ascending=False)
        rows.append(temprow[:5])
    return rows
listofterms=looping(listscript1)
test=pd.concat(listofterms)
alt.Chart(test).mark_point().encode(
    alt.X('term'),
    alt.Y('score'),
    alt.Color('link')
#     alt.Row('link')
)

alt.Chart(...)

In [11]:
pd.options.mode.chained_assignment = None  # default='warn'

def overtime(row, term):
    counts=row['script'].count(term)
    return counts
# filmscript['erin_count']=filmscript.apply(overtime, axis=1, term='erin')
merged2['erin_count']=merged2.apply(overtime, axis=1, term='erin')


In [12]:
alt.Chart(merged2).mark_point().encode(
    alt.X('erin_count', axis=alt.Axis(title='Erin count')),
    alt.Y('score', axis=alt.Axis(title='TFIDF score')),
    alt.Color('term')
)

alt.Chart(...)